In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from keras.layers import *
from keras.models import Sequential
from sklearn.preprocessing import LabelEncoder
import re
from keras.preprocessing.sequence import pad_sequences
from keras.preprocessing.text import Tokenizer
from keras.callbacks.callbacks import ModelCheckpoint

Using TensorFlow backend.


In [2]:
X=pd.read_csv("Train.csv")

In [3]:
Y=X["label"]

In [4]:
X=X.drop(columns=["label"])

In [5]:
X

review
0      mature intelligent and highly charged melodram...
1      http://video.google.com/videoplay?docid=211772...
2      Title: Opera (1987) Director: Dario Argento Ca...
3      I think a lot of people just wrote this off as...
4      This is a story of two dogs and a cat looking ...
...                                                  ...
39995  There are similarities between Ray Lawrence's ...
39996  For starters, I once met the director when he ...
39997  Much of "Over Her Dead Body" is so painfully u...
39998  "Lifeforce" is a truly bizarre adaptation of t...
39999  I saw this movie at a screener and its the bes...

[40000 rows x 1 columns]

In [6]:
Y

0        pos
1        pos
2        pos
3        pos
4        pos
        ... 
39995    neg
39996    neg
39997    neg
39998    pos
39999    pos
Name: label, Length: 40000, dtype: object

In [7]:
le=LabelEncoder()

In [8]:
Y=le.fit_transform(Y)

In [9]:
Y

array([1, 1, 1, ..., 0, 1, 1])

In [10]:
le.classes_

array(['neg', 'pos'], dtype=object)

In [11]:
X=np.array(X)

In [12]:
X=X.reshape(-1,)

In [13]:
X.shape

(40000,)

In [14]:
TAG_RE = re.compile(r'<[^>]+>')

def remove_tags(text):
    return TAG_RE.sub('', text)

In [15]:
def preprocess_text(sen):
    # Removing html tags
    sentence = remove_tags(sen)

    # Remove punctuations and numbers
    sentence = re.sub('[^a-zA-Z]', ' ', sentence)

    # Single character removal
    sentence = re.sub(r"\s+[a-zA-Z]\s+", ' ', sentence)

    # Removing multiple spaces
    sentence = re.sub(r'\s+', ' ', sentence)

    return sentence

In [16]:
X

array(["mature intelligent and highly charged melodrama unbelivebly filmed in China in 1948. wei wei's stunning performance as the catylast in a love triangle is simply stunning if you have the oppurunity to see this magnificent film take it",
       'http://video.google.com/videoplay?docid=211772166650071408&hl=en Distribution was tried.<br /><br />We opted for mass appeal.<br /><br />We want the best possible viewing range so, we forgo profit and continue our manual labor jobs gladly to entertain you for working yours.<br /><br />View Texas tale, please write about it... If you like it or not, if you like Alex or not, if you like Stuie, Texas or Texas tale... Just write about it.<br /><br />Your opinion rules.',
       "Title: Opera (1987) Director: Dario Argento Cast: Cristina Masillach, Ian Charleson, Urbano Barberini, Daria Nicolodi Review: The only other Argento movie I had seen was Suspiria and that one blew me away with its style, colors and spooky story line. I next decided to

In [17]:
for i in range(X.shape[0]):
    X[i]=preprocess_text(X[i])

In [18]:
X

array(['mature intelligent and highly charged melodrama unbelivebly filmed in China in wei wei stunning performance as the catylast in love triangle is simply stunning if you have the oppurunity to see this magnificent film take it',
       'http video google com videoplay docid hl en Distribution was tried We opted for mass appeal We want the best possible viewing range so we forgo profit and continue our manual labor jobs gladly to entertain you for working yours View Texas tale please write about it If you like it or not if you like Alex or not if you like Stuie Texas or Texas tale Just write about it Your opinion rules ',
       'Title Opera Director Dario Argento Cast Cristina Masillach Ian Charleson Urbano Barberini Daria Nicolodi Review The only other Argento movie had seen was Suspiria and that one blew me away with its style colors and spooky story line next decided to go with Opera as had been told it was one of his best Man think m discovering what will ultimately be one of 

In [19]:
emb={}
with open('glove.6B.100d.txt',encoding='utf-8') as f:
    for line in f:
        values=line.split()
        word=values[0]
        coeffs=np.asarray(values[1:],dtype='float32')

        emb[word]=coeffs

In [20]:
tokenizer=Tokenizer(num_words=10000)

In [21]:
tokenizer.fit_on_texts(X)

In [22]:
vocab_size=1+len(tokenizer.word_index)

In [23]:
vocab_size

92229

In [24]:
maxLen=200

In [25]:
X=tokenizer.texts_to_sequences(X)

In [26]:
X

[[2550,
  1067,
  2,
  528,
  5136,
  2518,
  736,
  7,
  2394,
  7,
  1418,
  234,
  11,
  1,
  7,
  106,
  4947,
  5,
  332,
  1418,
  40,
  17,
  23,
  1,
  4,
  59,
  8,
  1839,
  16,
  190,
  6],
 [5931,
  362,
  2279,
  4453,
  4948,
  10,
  734,
  64,
  13,
  3150,
  1311,
  64,
  175,
  1,
  114,
  606,
  778,
  1977,
  32,
  64,
  7707,
  2,
  1615,
  255,
  5672,
  2860,
  4,
  2736,
  17,
  13,
  758,
  6396,
  608,
  1928,
  788,
  582,
  863,
  39,
  6,
  40,
  17,
  34,
  6,
  36,
  19,
  40,
  17,
  34,
  2086,
  36,
  19,
  40,
  17,
  34,
  1928,
  36,
  1928,
  788,
  37,
  863,
  39,
  6,
  122,
  655,
  2249],
 [416,
  1245,
  155,
  8218,
  3812,
  174,
  3630,
  699,
  1,
  58,
  75,
  3812,
  12,
  63,
  104,
  10,
  2,
  9,
  24,
  4194,
  65,
  237,
  14,
  87,
  392,
  2628,
  2,
  3508,
  61,
  342,
  355,
  843,
  4,
  138,
  14,
  1245,
  11,
  63,
  72,
  552,
  6,
  10,
  24,
  3,
  22,
  114,
  120,
  97,
  147,
  4996,
  43,
  77,
  1119,
  25,
  24,
  

In [27]:
X=pad_sequences(X,padding='post',maxlen=maxLen)

In [28]:
X.shape

(40000, 200)

In [29]:
tokenizer.word_index.items()

dict_items([('the', 1), ('and', 2), ('of', 3), ('to', 4), ('is', 5), ('it', 6), ('in', 7), ('this', 8), ('that', 9), ('was', 10), ('as', 11), ('movie', 12), ('for', 13), ('with', 14), ('but', 15), ('film', 16), ('you', 17), ('on', 18), ('not', 19), ('he', 20), ('are', 21), ('his', 22), ('have', 23), ('one', 24), ('be', 25), ('at', 26), ('all', 27), ('they', 28), ('by', 29), ('an', 30), ('who', 31), ('so', 32), ('from', 33), ('like', 34), ('there', 35), ('or', 36), ('just', 37), ('her', 38), ('about', 39), ('if', 40), ('out', 41), ('has', 42), ('what', 43), ('some', 44), ('good', 45), ('can', 46), ('more', 47), ('when', 48), ('very', 49), ('she', 50), ('up', 51), ('no', 52), ('time', 53), ('even', 54), ('my', 55), ('would', 56), ('which', 57), ('only', 58), ('see', 59), ('really', 60), ('story', 61), ('their', 62), ('had', 63), ('we', 64), ('me', 65), ('well', 66), ('were', 67), ('much', 68), ('than', 69), ('bad', 70), ('get', 71), ('been', 72), ('do', 73), ('great', 74), ('other', 75),

In [30]:
embedding_matrix=np.zeros((vocab_size,100))

for word,idx in tokenizer.word_index.items():
    v=emb.get(word)
    if v is not None:
        embedding_matrix[idx]=v

In [31]:
embedding_matrix.shape

(92229, 100)

In [32]:
Y.shape

(40000,)

In [33]:
model=Sequential()
model.add(Embedding(vocab_size,100,weights=[embedding_matrix],input_length=200,trainable=False))
model.add(LSTM(128))
model.add(Dense(1,activation="sigmoid"))

In [34]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_1 (Embedding)      (None, 200, 100)          9222900   
_________________________________________________________________
lstm_1 (LSTM)                (None, 128)               117248    
_________________________________________________________________
dense_1 (Dense)              (None, 1)                 129       
Total params: 9,340,277
Trainable params: 117,377
Non-trainable params: 9,222,900
_________________________________________________________________


In [35]:
model.compile(optimizer='adam',loss='binary_crossentropy',metrics=["accuracy"])

In [41]:
from keras.utils import to_categorical

In [42]:
YOHT=to_categorical(Y)

In [36]:
checkpoint=ModelCheckpoint("model.h5",monitor='val_accuracy',save_best_only=True)

In [38]:
hist=model.fit(X,Y,epochs=2,validation_split=0.2,callbacks=[checkpoint])

Train on 32000 samples, validate on 8000 samples
Epoch 1/2
32000/32000 [==============================] - 290s 9ms/step - loss: 0.2953 - accuracy: 0.8762 - val_loss: 0.3198 - val_accuracy: 0.8616
Epoch 2/2
32000/32000 [==============================] - 287s 9ms/step - loss: 0.2793 - accuracy: 0.8833 - val_loss: 0.3035 - val_accuracy: 0.8671


In [69]:
model.load_weights('model.h5')

In [39]:
X_test=pd.read_csv("Test.csv")

In [40]:
X_test=np.array(X_test)

In [41]:
X_test=X_test.reshape(-1,)

In [42]:
X_test.shape

(10000,)

In [43]:
for i in range(X_test.shape[0]):
    X_test[i]=preprocess_text(X_test[i])

In [44]:
X_test=tokenizer.texts_to_sequences(X_test)

In [45]:
X_test

[[372,
  142,
  154,
  2297,
  2057,
  93,
  64,
  327,
  4,
  99,
  18,
  2357,
  2,
  2307,
  509,
  3067,
  48,
  255,
  185,
  64,
  67,
  7,
  2646,
  66,
  8,
  12,
  295,
  612,
  34,
  24,
  3,
  142,
  93,
  1095,
  2347,
  4,
  1919,
  10,
  1,
  106,
  602,
  4,
  3516,
  5771,
  100,
  7,
  6147,
  2971,
  2,
  8,
  234,
  10,
  24,
  3,
  1,
  975,
  133,
  50,
  107,
  86,
  6,
  189,
  50,
  127,
  373,
  519,
  7,
  6147,
  2971,
  185,
  50,
  10,
  994,
  994,
  188,
  4,
  803,
  41,
  44,
  3,
  1,
  75,
  93,
  50,
  72,
  7,
  569,
  1336,
  203,
  1336,
  4,
  868,
  156,
  189,
  273,
  176,
  57,
  524,
  10,
  19,
  1484,
  14,
  345,
  15,
  11,
  1514,
  11,
  50,
  5,
  4,
  55,
  506,
  55,
  1254,
  26,
  65,
  4,
  469,
  6,
  118,
  80,
  50,
  249,
  156,
  679,
  698,
  214,
  2,
  218,
  6,
  49,
  901,
  7,
  8,
  12,
  394,
  11,
  2,
  19,
  45,
  24,
  345,
  31,
  758,
  1,
  7508,
  3,
  1952,
  406,
  584,
  6,
  7,
  38,
  199,
  32,
  50,
  

In [46]:
X_test=pad_sequences(X_test,padding='post',maxlen=maxLen)

In [47]:
X_test.shape

(10000, 200)

In [48]:
hist.history["val_accuracy"]

[0.8616250157356262, 0.8671249747276306]

In [49]:
reviews=model.predict(X_test)

In [50]:
reviews

array([[0.02882588],
       [0.68886214],
       [0.00843894],
       ...,
       [0.9765717 ],
       [0.9777913 ],
       [0.38089383]], dtype=float32)

In [51]:
reviews[reviews<0.5]=0
reviews[reviews>=0.5]=1

In [52]:
reviews

array([[0.],
       [1.],
       [0.],
       ...,
       [1.],
       [1.],
       [0.]], dtype=float32)

In [53]:
id_matrix=[]
for i in range(X_test.shape[0]):
    id_matrix.append(i)

In [54]:
id_matrix=np.array(id_matrix)
id_matrix=id_matrix.reshape(-1,1)

In [55]:
id_matrix.shape

(10000, 1)

In [56]:
d={1:"pos",0:"neg"}

In [57]:
reviews=reviews.reshape(-1,)

In [58]:
int_rev=np.array(reviews,dtype='int64')

In [59]:
int_rev

array([0, 1, 0, ..., 1, 1, 0], dtype=int64)

In [60]:
final_rev=[d[x] for x in int_rev]

In [61]:
final_rev=np.array(final_rev)

In [62]:
final_rev=final_rev.reshape(-1,1)

In [63]:
final_rev

array([['neg'],
       ['pos'],
       ['neg'],
       ...,
       ['pos'],
       ['pos'],
       ['neg']], dtype='<U3')

In [64]:
stacked=np.hstack((id_matrix,final_rev))

In [65]:
stacked

array([['0', 'neg'],
       ['1', 'pos'],
       ['2', 'neg'],
       ...,
       ['9997', 'pos'],
       ['9998', 'pos'],
       ['9999', 'neg']], dtype='<U11')

In [66]:
pred=pd.DataFrame(stacked,columns=["Id","label"])

In [67]:
pred

Id label
0        0   neg
1        1   pos
2        2   neg
3        3   pos
4        4   pos
...    ...   ...
9995  9995   neg
9996  9996   pos
9997  9997   pos
9998  9998   pos
9999  9999   neg

[10000 rows x 2 columns]

In [68]:
pred.to_csv("pred.csv",index=False)